In [ ]:
import pandas as pd
import nltk
# nltk.download('all')
import re
import numpy as np
import collections
import sklearn as sk
import string

In [22]:
# df = pd.read_csv("../B_Data_Cleaning/synthetic_reviews_all.csv")
df = pd.read_csv("../B_Data_Cleaning/synthetic_reviews_all_trial.csv")
df["Review"] = df["Review"].astype("str")
df

Review  \
0      ультра exploiters swaying bem sinced footright...   
1      punkedup left nonimmersive sold representing b...   
2      aestethic slums господи iextend тяжелее weirdn...   
3      chemicals exmple carpenter gunz homosexual dep...   
4       uneventful bugsaways whispered mojave cutremoved   
...                                                  ...   
16570  nonimmersive bloggers ubthis animes cone intri...   
16571  roleplayb parkor seeking funneling expanded ch...   
16572  insignificant holotape adultstuff ssh aprimora...   
16573  intensely thinkmaybe antenna iceskate okeish a...   
16574  uprosu spoilerhighly jk awesome toolplaystyle ...   

       Recommended or Not Recommended  
0                                True  
1                                True  
2                                True  
3                                True  
4                                True  
...                               ...  
16570                           False  
16571                           False  
16572                           False  
16573                           False  
16574                           False  

[16575 rows x 2 columns]

In [23]:
# make a set_column to count the number of words in each review
df["set_column"] = df["Review"].apply(lambda x: set(x.split()))
df

Review  \
0      ультра exploiters swaying bem sinced footright...   
1      punkedup left nonimmersive sold representing b...   
2      aestethic slums господи iextend тяжелее weirdn...   
3      chemicals exmple carpenter gunz homosexual dep...   
4       uneventful bugsaways whispered mojave cutremoved   
...                                                  ...   
16570  nonimmersive bloggers ubthis animes cone intri...   
16571  roleplayb parkor seeking funneling expanded ch...   
16572  insignificant holotape adultstuff ssh aprimora...   
16573  intensely thinkmaybe antenna iceskate okeish a...   
16574  uprosu spoilerhighly jk awesome toolplaystyle ...   

       Recommended or Not Recommended  \
0                                True   
1                                True   
2                                True   
3                                True   
4                                True   
...                               ...   
16570                           False   
16571                           False   
16572                           False   
16573                           False   
16574                           False   

                                              set_column  
0      {ofuscante, damnnn, prayed, 없음, snails, slack,...  
1      {luster, skied, patchedbut, brigitte, bf, hamm...  
2      {armorgear, gamecodes, alphabet, canon, iq, at...  
3      {staring, achieved, choiceswhat, crafty, count...  
4      {bugsaways, cutremoved, uneventful, mojave, wh...  
...                                                  ...  
16570  {guitaring, learn, dmgcalculation, equally, he...  
16571  {vacant, cores, قاعد, brain, noodles, worldfil...  
16572  {ssh, moneycrafting, native, bonnes, vs, subje...  
16573  {unfairly, полиции, seedetect, acabado, androm...  
16574  {swotor, hab, laterstill, pilot, expletives, g...  

[16575 rows x 3 columns]

In [24]:
# keep only 5250 reviews for each based on 'Recommended or Not Recommended" column
temp_recom = df.loc[df["Recommended or Not Recommended"] == True,:]
temp_recom = temp_recom.sample(5250).reset_index(drop=True)

temp_not_recom = df.loc[df["Recommended or Not Recommended"] == False,:]
temp_not_recom = temp_not_recom.sample(5250).reset_index(drop=True)

# combine temp_recom and temp_not_recom
temp = pd.concat([temp_recom, temp_not_recom], axis=0).reset_index(drop=True)

# split the data into train and test
train, test = sk.model_selection.train_test_split(temp, test_size=0.33, random_state=42)

# # split df_recom into train and test
# df_recom = temp_recom.sample(frac=0.67, random_state=42).reset_index(drop=True)
# test_recom = temp_recom.drop(df_recom.index).reset_index(drop=True)
# print(f"train size df_recom: {len(df_recom)}, test size df_recom: {len(test_recom)}")

# # split df_not_recom into train and test
# df_not_recom = temp_not_recom.sample(frac=0.33, random_state=42).reset_index(drop=True)
# test_not_recom = temp_not_recom.drop(df_not_recom.index).reset_index(drop=True)
# print(f"train size df_not_recom: {len(df_not_recom)}, test size df_not_recom: {len(test_not_recom)}")

# # combine test_recom and test_not_recom
# test = pd.concat([test_recom, test_not_recom], axis=0).reset_index(drop=True)

In [25]:
# Dividing dataset into recommended and not recommended
df_recom = train.loc[train["Recommended or Not Recommended"] == True,:]
df_recom = df_recom.reset_index(drop=True)

df_not_recom = train.loc[train["Recommended or Not Recommended"] == False,:]
df_not_recom = df_not_recom.reset_index(drop=True)

In [26]:
# This is to make the set dictionary
# count how many times each word appears in the reviews
bow_recom_temp = collections.Counter([y for x in df_recom.set_column for y in x])
bow_not_recom_temp = collections.Counter([y for x in df_not_recom.set_column for y in x])

bow_recom_set = dict(bow_recom_temp)
bow_not_recom_set = dict(bow_not_recom_temp)

for key in bow_recom_set:
    if key not in bow_not_recom_set:
        bow_not_recom_set[key] = 0
        pass
    else:
        pass

for key in bow_not_recom_set:
    if key not in bow_recom_set:
        bow_recom_set[key] = 0
        pass
    else:
        pass

for key in bow_recom_set:
    bow_recom_set[key] += 1

for key in bow_not_recom_set:
    bow_not_recom_set[key] += 1


In [27]:
# This is to make the list dictionary
# count how many times each word appears in the reviews
bow_recom = collections.Counter([y for x in df_recom.Review for y in x.split()])
bow_not_recom = collections.Counter([y for x in df_not_recom.Review for y in x.split()])

bow_recom_dict = dict(bow_recom)
bow_not_recom_dict = dict(bow_not_recom)

for key in bow_recom_dict:
    if key not in bow_not_recom_dict:
        bow_not_recom_dict[key] = 0
        pass
    else:
        pass

for key in bow_not_recom_dict:
    if key not in bow_recom_dict:
        bow_recom_dict[key] = 0
        pass
    else:
        pass

for key in bow_recom_dict:
    bow_recom_dict[key] += 1

for key in bow_not_recom_dict:
    bow_not_recom_dict[key] += 1
    

In [28]:
bow_recom_sum_vals = sum(bow_recom_dict.values())
bow_not_recom_sum_vals = sum(bow_not_recom_dict.values())

for i in bow_recom_dict:

    bow_recom_dict[i] /= bow_recom_sum_vals

for i in bow_not_recom_dict:

    bow_not_recom_dict[i] /= bow_not_recom_sum_vals

In [29]:
assert len(bow_recom_dict) == len(bow_not_recom_dict)
assert len(bow_recom_set) == len(bow_not_recom_set)

In [30]:
test.drop(columns=["set_column"], inplace=True)

In [31]:
def define_sentiment_all(element,test1=False, test2=False):

    """This function takes a review and returns the label for that review"""

    full_shape = df.shape[0]
    positive_review_probabiliy = len(df_recom)/full_shape
    negative_review_probabiliy = len(df_not_recom)/full_shape
    
    df_choices_positive = [positive_review_probabiliy, bow_recom_set, bow_recom_dict, df_recom]
    df_choices_negative = [negative_review_probabiliy ,bow_not_recom_set, bow_not_recom_dict, df_not_recom]

    def classifier(element, your_class = 'positive'):
        flag = {}
        flag_count = 0
        if your_class == 'positive':
            df_choices = df_choices_positive
        else:
            df_choices = df_choices_negative
        prob_of_class = df_choices[0]/full_shape
        score = 1 * prob_of_class
        score = float(format(score, '.12f'))
        # score = 0.1
        for i in element.split():
            if i not in df_choices[2].keys():
                pass
            else:
                prob_word_given_class = (df_choices[2])[i]
                prob_word_given_class = float(format(prob_word_given_class, '.12f'))
                # Almost the same value, given our spin on this application. 
                # Normally, this term frequency would be calculated differently across the positive and negative documents
                # but we are only looking at the reviews as the documents themselves to determine a word's relevance in the positive
                # or negative corpus. 
                tf = np.log(prob_word_given_class)
                # tf = float(format(tf, '.12f'))
                # tf = abs(np.log(prob_word_given_class))
                # The IDF is the number of reviews / the number of reviews that contain the word in that given corpus
                # idf = abs(np.log(df_choices[3].shape[0]/(df_choices[1])[i]))
                idf = np.log(df_choices[3].shape[0]/(df_choices[1])[i])
                # idf = float(format(idf, '.12f'))
                score *= prob_word_given_class*tf*idf
                # score *= prob_word_given_class*idf
                # score *= prob_word_given_class*tf
                # score *= prob_word_given_class

                if score < 0:
                    flag[flag_count] = (score, your_class)
                    print(flag_count,i)
                    flag_count += 1


        return score
    positive_score = classifier(element, 'positive')
    negative_score = classifier(element, 'negative')
    if positive_score > negative_score:
        return True
    elif positive_score == negative_score:
        # Choosing an arbitrary value, because we assume that a review with one or few words of little substance
        # is implied to be negative, as is usual with netizens. 
        return False
    else:
        return False

In [32]:
def define_sentiment_idf(element,test1=False, test2=False):

    """This function takes a review and returns the label for that review"""

    full_shape = df.shape[0]
    positive_review_probabiliy = len(df_recom)/full_shape
    negative_review_probabiliy = len(df_not_recom)/full_shape
    
    df_choices_positive = [positive_review_probabiliy, bow_recom_set, bow_recom_dict, df_recom]
    df_choices_negative = [negative_review_probabiliy ,bow_not_recom_set, bow_not_recom_dict, df_not_recom]

    def classifier(element, your_class = 'positive'):
        flag = {}
        flag_count = 0
        if your_class == 'positive':
            df_choices = df_choices_positive
        else:
            df_choices = df_choices_negative
        prob_of_class = df_choices[0]/full_shape
        score = 1 * prob_of_class
        score = float(format(score, '.12f'))
        # score = 0.1
        for i in element.split():
            if i not in df_choices[2].keys():
                pass
            else:
                prob_word_given_class = (df_choices[2])[i]
                prob_word_given_class = float(format(prob_word_given_class, '.12f'))
                # Almost the same value, given our spin on this application. 
                # Normally, this term frequency would be calculated differently across the positive and negative documents
                # but we are only looking at the reviews as the documents themselves to determine a word's relevance in the positive
                # or negative corpus. 
                tf = np.log(prob_word_given_class)
                # tf = float(format(tf, '.12f'))
                # tf = abs(np.log(prob_word_given_class))
                # The IDF is the number of reviews / the number of reviews that contain the word in that given corpus
                # idf = abs(np.log(df_choices[3].shape[0]/(df_choices[1])[i]))
                idf = np.log(df_choices[3].shape[0]/(df_choices[1])[i])
                # idf = float(format(idf, '.12f'))
                # score *= prob_word_given_class*tf*idf
                score *= prob_word_given_class*idf
                # score *= prob_word_given_class*tf
                # score *= prob_word_given_class

                if score < 0:
                    flag[flag_count] = (score, your_class)
                    print(flag_count,i)
                    flag_count += 1


        return score
    positive_score = classifier(element, 'positive')
    negative_score = classifier(element, 'negative')
    if positive_score > negative_score:
        return True
    elif positive_score == negative_score:
        # Choosing an arbitrary value, because we assume that a review with one or few words of little substance
        # is implied to be negative, as is usual with netizens. 
        return False
    else:
        return False

In [33]:
def define_sentiment_tf(element,test1=False, test2=False):

    """This function takes a review and returns the label for that review"""

    full_shape = df.shape[0]
    positive_review_probabiliy = len(df_recom)/full_shape
    negative_review_probabiliy = len(df_not_recom)/full_shape
    
    df_choices_positive = [positive_review_probabiliy, bow_recom_set, bow_recom_dict, df_recom]
    df_choices_negative = [negative_review_probabiliy ,bow_not_recom_set, bow_not_recom_dict, df_not_recom]

    def classifier(element, your_class = 'positive'):
        flag = {}
        flag_count = 0
        if your_class == 'positive':
            df_choices = df_choices_positive
        else:
            df_choices = df_choices_negative
        prob_of_class = df_choices[0]/full_shape
        score = 1 * prob_of_class
        score = float(format(score, '.12f'))
        # score = 0.1
        for i in element.split():
            if i not in df_choices[2].keys():
                pass
            else:
                prob_word_given_class = (df_choices[2])[i]
                prob_word_given_class = float(format(prob_word_given_class, '.12f'))
                # Almost the same value, given our spin on this application. 
                # Normally, this term frequency would be calculated differently across the positive and negative documents
                # but we are only looking at the reviews as the documents themselves to determine a word's relevance in the positive
                # or negative corpus. 
                tf = np.log(prob_word_given_class)
                # tf = float(format(tf, '.12f'))
                # tf = abs(np.log(prob_word_given_class))
                # The IDF is the number of reviews / the number of reviews that contain the word in that given corpus
                # idf = abs(np.log(df_choices[3].shape[0]/(df_choices[1])[i]))
                idf = np.log(df_choices[3].shape[0]/(df_choices[1])[i])
                # idf = float(format(idf, '.12f'))
                # score *= prob_word_given_class*tf*idf
                # score *= prob_word_given_class*idf
                score *= prob_word_given_class*tf
                # score *= prob_word_given_class

                if score < 0:
                    flag[flag_count] = (score, your_class)
                    print(flag_count,i)
                    flag_count += 1


        return score
    positive_score = classifier(element, 'positive')
    negative_score = classifier(element, 'negative')
    if positive_score > negative_score:
        return True
    elif positive_score == negative_score:
        # Choosing an arbitrary value, because we assume that a review with one or few words of little substance
        # is implied to be negative, as is usual with netizens. 
        return False
    else:
        return False

In [34]:
def define_sentiment_freq(element,test1=False, test2=False):

    """This function takes a review and returns the label for that review"""

    full_shape = df.shape[0]
    positive_review_probabiliy = len(df_recom)/full_shape
    negative_review_probabiliy = len(df_not_recom)/full_shape
    
    df_choices_positive = [positive_review_probabiliy, bow_recom_set, bow_recom_dict, df_recom]
    df_choices_negative = [negative_review_probabiliy ,bow_not_recom_set, bow_not_recom_dict, df_not_recom]

    def classifier(element, your_class = 'positive'):
        flag = {}
        flag_count = 0
        if your_class == 'positive':
            df_choices = df_choices_positive
        else:
            df_choices = df_choices_negative
        prob_of_class = df_choices[0]/full_shape
        score = 1 * prob_of_class
        score = float(format(score, '.12f'))
        # score = 0.1
        for i in element.split():
            if i not in df_choices[2].keys():
                pass
            else:
                prob_word_given_class = (df_choices[2])[i]
                prob_word_given_class = float(format(prob_word_given_class, '.12f'))
                # Almost the same value, given our spin on this application. 
                # Normally, this term frequency would be calculated differently across the positive and negative documents
                # but we are only looking at the reviews as the documents themselves to determine a word's relevance in the positive
                # or negative corpus. 
                tf = np.log(prob_word_given_class)
                # tf = float(format(tf, '.12f'))
                # tf = abs(np.log(prob_word_given_class))
                # The IDF is the number of reviews / the number of reviews that contain the word in that given corpus
                # idf = abs(np.log(df_choices[3].shape[0]/(df_choices[1])[i]))
                idf = np.log(df_choices[3].shape[0]/(df_choices[1])[i])
                # idf = float(format(idf, '.12f'))
                # score *= prob_word_given_class*tf*idf
                # score *= prob_word_given_class*idf
                # score *= prob_word_given_class*tf
                score *= prob_word_given_class

                if score < 0:
                    flag[flag_count] = (score, your_class)
                    print(flag_count,i)
                    flag_count += 1


        return score
    positive_score = classifier(element, 'positive')
    negative_score = classifier(element, 'negative')
    if positive_score > negative_score:
        return True
    elif positive_score == negative_score:
        # Choosing an arbitrary value, because we assume that a review with one or few words of little substance
        # is implied to be negative, as is usual with netizens. 
        return False
    else:
        return False

In [35]:
test["score_all"] = test.Review.apply(define_sentiment_all)
test["score_tf"] = test.Review.apply(define_sentiment_tf)
test["score_idf"] = test.Review.apply(define_sentiment_idf)
test["score_freq"] = test.Review.apply(define_sentiment_freq)

0 eyecatching
1 cranked
2 armorcrafting
0 eyecatching
1 cranked
2 armorcrafting
0 vector
1 hpc
2 nomade
3 وقراند
4 pamspoiler
5 exagerating
6 rpgsame
7 shortcomings
8 tank
9 eigter
10 proverbially
11 hustling
12 hayatımın
0 vector
1 hpc
2 nomade
3 وقراند
4 pamspoiler
5 exagerating
6 rpgsame
7 shortcomings
8 tank
9 eigter
10 proverbially
11 hustling
12 hayatımın
0 были
1 complex
2 transcend
3 fight
4 dieser
5 underworked
6 lod
7 sourcebooks
8 transferring
9 pushed
10 рассеивания
11 take
12 intrinsically
13 update
14 быстрой
15 좋은게
16 moterbike
17 faced
18 harmlessnon
19 monitorstd
20 pedigree
21 purchaseb
22 stalling
23 spoils
24 predefined
25 madly
26 selfaware
27 disabling
28 placesshops
29 flashlight
30 suffering
31 hrtx
32 disposable
33 shelf
34 senses
35 moonlights
36 bending
0 были
1 complex
2 transcend
3 fight
4 dieser
5 underworked
6 lod
7 sourcebooks
8 transferring
9 pushed
10 рассеивания
11 take
12 intrinsically
13 update
14 быстрой
15 좋은게
16 moterbike
17 faced
18 harmlessnon


In [36]:
print(f"This is our accuracy for (balanced) synthetic data when we use all the formula: {(sum(test['Recommended or Not Recommended'] == test['score_all'])/test.shape[0])*100:.2f}%")
print(f"This is our accuracy for (balanced) synthetic data when we use only frequency and TF: {(sum(test['Recommended or Not Recommended'] == test['score_tf'])/test.shape[0])*100:.2f}%")
print(f"This is our accuracy for (balanced) synthetic data when we use only frequency and IDF: {(sum(test['Recommended or Not Recommended'] == test['score_idf'])/test.shape[0])*100:.2f}%")
print(f"This is our accuracy for (balanced) synthetic data when we use only frequency: {(sum(test['Recommended or Not Recommended'] == test['score_freq'])/test.shape[0])*100:.2f}%")

This is our accuracy for (balanced) synthetic data when we use all the formula: 51.11%
This is our accuracy for (balanced) synthetic data when we use only frequency and TF: 50.82%
This is our accuracy for (balanced) synthetic data when we use only frequency and IDF: 51.20%
This is our accuracy for (balanced) synthetic data when we use only frequency: 50.53%


In [37]:
# Generate a confusion matrix
from sklearn.metrics import confusion_matrix
confusion_matrix(test['Recommended or Not Recommended'], test['score_all'])
# Generate a classification report
from sklearn.metrics import classification_report
print(classification_report(test['Recommended or Not Recommended'], test['score_all']))


              precision    recall  f1-score   support

       False       0.50      0.60      0.55      1699
        True       0.53      0.42      0.47      1766

    accuracy                           0.51      3465
   macro avg       0.51      0.51      0.51      3465
weighted avg       0.51      0.51      0.51      3465



In [38]:
# Generate a confusion matrix
from sklearn.metrics import confusion_matrix
confusion_matrix(test['Recommended or Not Recommended'], test['score_tf'])
# Generate a classification report
from sklearn.metrics import classification_report
print(classification_report(test['Recommended or Not Recommended'], test['score_tf']))


              precision    recall  f1-score   support

       False       0.50      0.62      0.55      1699
        True       0.52      0.40      0.45      1766

    accuracy                           0.51      3465
   macro avg       0.51      0.51      0.50      3465
weighted avg       0.51      0.51      0.50      3465



In [39]:
# Generate a confusion matrix
from sklearn.metrics import confusion_matrix
confusion_matrix(test['Recommended or Not Recommended'], test['score_idf'])
# Generate a classification report
from sklearn.metrics import classification_report
print(classification_report(test['Recommended or Not Recommended'], test['score_idf']))


              precision    recall  f1-score   support

       False       0.50      0.55      0.53      1699
        True       0.52      0.47      0.50      1766

    accuracy                           0.51      3465
   macro avg       0.51      0.51      0.51      3465
weighted avg       0.51      0.51      0.51      3465



In [40]:
# Generate a confusion matrix
from sklearn.metrics import confusion_matrix
confusion_matrix(test['Recommended or Not Recommended'], test['score_freq'])
# Generate a classification report
from sklearn.metrics import classification_report
print(classification_report(test['Recommended or Not Recommended'], test['score_freq']))


              precision    recall  f1-score   support

       False       0.50      0.69      0.58      1699
        True       0.52      0.33      0.40      1766

    accuracy                           0.51      3465
   macro avg       0.51      0.51      0.49      3465
weighted avg       0.51      0.51      0.49      3465

